In [117]:
import os
import json
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
date = '2019-12-20_21'
date = 'noProxy/All'
root_dir = '/Users/Leo/Documents/github/GradProj/'
N = 15
Proportion = 0.8

In [118]:
#stream_tag_path = root_dir + 'DataSet/result/' + date + '/stream_tag.txt'
stream_tag_path = root_dir + 'DataSet/result/' + date + '/stream_tag.txt'
stream_tag_pd = pd.read_table(stream_tag_path, sep='\s+', header=None)
stream_tag_pd.iloc[:,3]=443
stream_tag_map = {tuple(x[0:4]):x[4] for x in list(stream_tag_pd.values)}
print('end2')

end2


In [119]:
stream_bursd_l = list()
stream_length_l = list()
stream_type_l = list()
stream_label = list()
#stream_bytes_l = list()
#stream_feature_path = root_dir + 'DataSet/result/' + date + '/stream_stat.txt'
stream_feature_path = root_dir + 'DataSet/result/' + date + '/stream_stat.txt'
stream_feature_f = open(stream_feature_path, 'r')
i = 0
for line in stream_feature_f.readlines():
    stream_feature_json = json.loads(line)
    try:
        key = (stream_feature_json['sip'], stream_feature_json['sport'], stream_feature_json['dip'], stream_feature_json['dport'])
        stream_label.append(stream_tag_map[key])
        i += 1
    except Exception:
        continue
    packets = stream_feature_json['packets']
    tls_message_list = stream_feature_json['tls']['tls_message_list']
    stream_length = [tls_message['length'] for tls_message in tls_message_list]
    stream_type = [tls_message['type'] for tls_message in tls_message_list]
    #stream_length.append((stream_feature_json['sip'], stream_feature_json['sport'], stream_feature_json['dip'], stream_feature_json['dport']))
    stream_burst = list()
    burst_length = 0
#    stream_bytes = list()
    old_dir = 0
    for j,packet in enumerate(packets):
#        stream_bytes.append(packet['bytes'])
        if j == 0:
            burst_length = packet['bytes']
            old_dir = packet['dir']
            continue
        if old_dir == packet['dir']:
            burst_length += packet['bytes']
            continue
        if old_dir != packet['dir']:
            stream_burst.append(burst_length)
            old_dir = packet['dir']
            burst_length = packet['bytes']
#    stream_bytes_l.append(stream_bytes)
    stream_burst.append(burst_length)
    
    #取前10个，20个，30个
    if N != -1:
        stream_length = stream_length[0:N]
        stream_type = stream_type[0:N]
        stream_burst = stream_burst[0:N]
    
    stream_length_l.append(stream_length)
    stream_type_l.append(stream_type)
    stream_bursd_l.append(stream_burst)
stream_length_array = np.array(stream_length_l)
stream_type_array = np.array(stream_type_l)
stream_burst_array = np.array(stream_bursd_l)
len(stream_length_array)
#stream_bytes_array = np.array(stream_bytes_l)

34686

In [120]:
stream_burst_array

array([[180, 4541, 126, 51, 333, 185265],
       [212, 4541, 126, 51, 334, 264020], [181, 4541, 126, 51, 380, 98029],
       ...,
       [180, 3582, 126, 51, 506, 195, 46, 42, 46, 42, 46, 42, 46, 42, 46],
       [517, 133, 941, 444, 1048, 411, 934, 362, 1048, 411, 1093, 343, 1093, 343, 1093],
       [517, 3591, 126, 120, 2831, 299, 206, 219, 364, 219, 232, 219, 5577, 261, 4171]], dtype=object)

In [121]:
stream_length_array

array([[175, 93, 4091, 333, 4, 70, 1, 40, 1, 40, 328, 5863, 16408, 16408, 16408],
       [207, 93, 4091, 333, 4, 70, 1, 40, 1, 40, 329, 2944, 16408, 16408, 16408],
       [176, 93, 4091, 333, 4, 70, 1, 40, 1, 40, 375, 2942, 16408, 16408, 16408],
       ...,
       [175, 89, 3136, 333, 4, 70, 1, 40, 1, 40, 501, 190, 41, 37, 41],
       [512, 85, 1, 32, 1, 32, 735, 153, 439, 733, 305, 406, 743, 181, 357],
       [512, 98, 3136, 333, 4, 70, 1, 40, 1, 40, 64, 48, 45, 37, 247]], dtype=object)

In [122]:
stream_type_array

array([[1, 2, 8, 9, 11, 13, 21, 26, 21, 26, 23, 23, 23, 23, 23],
       [1, 2, 8, 9, 11, 13, 21, 4, 21, 4, 23, 23, 23, 23, 23],
       [1, 2, 8, 9, 11, 13, 21, 26, 21, 26, 23, 23, 23, 23, 23], ...,
       [1, 2, 8, 9, 11, 13, 21, 26, 21, 26, 23, 23, 23, 23, 23],
       [1, 2, 21, 26, 21, 14, 23, 23, 23, 23, 23, 23, 23, 23, 23],
       [1, 2, 8, 9, 11, 13, 21, 0, 21, 26, 23, 23, 23, 23, 23]], dtype=object)

In [123]:
stream_type_dict = dict()
stream_length_dict = dict()
stream_burst_dict = dict()
for i in range(len(stream_type_l)):
    stream_type = stream_type_l[i]
    stream_length = stream_length_l[i]
    stream_burst = stream_bursd_l[i]
    if stream_label[i] not in stream_type_dict:
        stream_type_dict[stream_label[i]] = list()
        stream_type_dict[stream_label[i]].append(stream_type)
        stream_length_dict[stream_label[i]] = list()
        stream_length_dict[stream_label[i]].append(stream_length)
        stream_burst_dict[stream_label[i]] = list()
        stream_burst_dict[stream_label[i]].append(stream_burst)
    else :
        stream_type_dict[stream_label[i]].append(stream_type)
        stream_length_dict[stream_label[i]].append(stream_length)
        stream_burst_dict[stream_label[i]].append(stream_burst)
pd.Series(stream_label).value_counts()
stream_burst_dict

{'alipay': [[180, 4541, 126, 51, 333, 185265],
  [212, 4541, 126, 51, 334, 264020],
  [181, 4541, 126, 51, 380, 98029],
  [212, 4541, 126, 51, 627, 14403],
  [212, 4541, 126, 51, 613, 12503],
  [172, 3383, 126, 51, 601, 14920],
  [212, 4541, 126, 51, 632, 36444],
  [212, 4541, 126, 51, 639, 23530],
  [212, 4541, 126, 51, 617, 94706],
  [212, 4541, 126, 51, 635, 115414],
  [212, 4541, 126, 51, 621, 129243],
  [212, 4541, 126, 51, 630, 251546],
  [212, 4541, 126, 51, 334, 52585],
  [212, 4541, 126, 51, 334, 232560],
  [177, 4541, 126, 51, 871, 3932],
  [212, 141, 642, 3762],
  [212, 4541, 126, 51, 673, 3101],
  [212, 4541, 126, 51, 673, 3885],
  [212, 4541, 126, 51, 673, 2831],
  [212, 4541, 126, 51, 673, 4653],
  [212, 4541, 126, 51, 673, 4639],
  [212, 4541, 126, 51, 673, 4128],
  [212, 4541, 126, 51, 673, 3745],
  [173, 3383, 126, 51, 667, 6881],
  [212, 4541, 126, 51, 673, 5298],
  [212, 4541, 126, 51, 673, 11617],
  [212, 4541, 126, 51, 673, 6149],
  [212, 4541, 126, 51, 673, 20721]

In [124]:
import random
def divide_train(stream_dict):
    stream_train_dict = dict()
    for key, value in stream_dict.items():
        random.shuffle(value)
        stream_train_dict[key] = value[:int(len(value)*0.75)]
    return stream_train_dict
def divide_test(stream_dict):
    stream_test_dict = dict()
    for key, value in stream_dict.items():
        random.shuffle(value)
        stream_test_dict[key] = value[int(len(value)*0.75):]
    return stream_test_dict
stream_type_train_dict = divide_train(stream_type_dict)
stream_length_train_dict = divide_train(stream_length_dict)
stream_burst_train_dict = divide_train(stream_burst_dict)
stream_type_test_dict = divide_test(stream_type_dict)
stream_length_test_dict = divide_test(stream_length_dict)
stream_burst_test_dict = divide_test(stream_burst_dict)
#len(stream_type_dict)
#stream_burst_train_dict

In [125]:
#type markov start and end state
type_start_state = dict()
type_end_state = dict()
#transition_matrix = np.zero((27,27))
for key,value in stream_type_train_dict.items():
    start_state = pd.Series([line[0] for line in value]).value_counts()
    end_state = pd.Series([line[-1] for line in value]).value_counts()
    type_start_state[key] = start_state/start_state.sum()
    type_end_state[key] = end_state/end_state.sum()

print('end2')

end2


In [126]:
#type markov transition_matrix
type_transition_matrix = {key : pd.DataFrame(np.zeros((27,27))) for key in stream_type_train_dict.keys()}
for key,value in stream_type_test_dict.items():
    t_value  = type_transition_matrix[key]
    for line in value:
        for i,i_value in enumerate(line):
            if i == len(line) - 1:
                break
            t_value.iloc[i_value,line[i+1]] += 1
    type_transition_matrix[key] = t_value.apply(lambda x:x/x.sum(),axis = 'columns').fillna(0)
#type_transition_matrix['weibo']
print('end2')

end2


In [127]:
#length markov start and end state
length_count = dict()
for key,value in stream_length_train_dict.items():
    length_count[key] = dict()
    for line in value:
        for i in line:
            if i not in length_count[key]:
                length_count[key][i] = 1
            else :
                length_count[key][i] += 1
    length_count[key] = pd.Series(length_count[key]).sort_values(ascending=False)
#len(length_count['weibo'])
print('end2')

end2


In [128]:
length_list = dict()
for key,value in length_count.items():
    length_list[key] = dict()
    length_sum = 0
    pos = 0
    for i in range(len(value)):
        if length_sum >= value.sum()*Proportion:# or value.iloc[i] <= 1:
            break
        length_sum += value.iloc[i]
        length_list[key][value.index[i]] = pos
        pos += 1
#len(length_list['weibo'])
print('end2')

end2


In [129]:
stream_length_cdict = dict()
for key,value in stream_length_train_dict.items():
    change_list = length_list[key].keys()
    for i,line in enumerate(value):
        change_line = [min(change_list, key=lambda x:abs(x-i)) for i in line]
        value[i] = change_line
    stream_length_cdict[key] = value
print('end2')

end2


In [130]:
length_start_state = dict()
length_end_state = dict()
for key,value in stream_length_cdict.items():
    length_start_state[key] = pd.Series([length_list[key][x[0]] for x in value]).value_counts()
    length_end_state[key] = pd.Series([length_list[key][x[-1]] for x in value]).value_counts()
    length_start_state[key] = length_start_state[key]/length_start_state[key].sum()
    length_end_state[key] = length_end_state[key]/length_end_state[key].sum()
print('end2')

end2


In [131]:
#length transition matrix
length_transition_matrix = dict()

for key,value in stream_length_cdict.items():
    shape = (len(length_list[key]),len(length_list[key]))
    transition = pd.DataFrame(np.zeros(shape))
    for line in value:
        for i,x in enumerate(line):
            if i >= len(line)-1:
                break
            transition.iloc[length_list[key][x], length_list[key][line[i+1]]] += 1
    length_transition_matrix[key] = transition.apply(lambda x:x/x.sum(),axis = 'columns').fillna(0)
#print(length_transition_matrix['chrome'].iloc[5,24])
print('end2')

end2


In [132]:
#burst markov start and end state
burst_count = dict()
for key,value in stream_burst_train_dict.items():
    burst_count[key] = dict()
    for line in value:
        for i in line:
            if i not in burst_count[key]:
                burst_count[key][i] = 1
            else :
                burst_count[key][i] += 1
    burst_count[key] = pd.Series(burst_count[key]).sort_values(ascending=False)
print('end2')

end2


In [133]:
burst_list = dict()
for key,value in burst_count.items():
    burst_list[key] = dict()
    burst_sum = 0
    pos = 0
    for i in range(len(value)):
        if burst_sum >= value.sum()*Proportion:# or value.iloc[i] <= 1:
            break
        burst_sum += value.iloc[i]
        burst_list[key][value.index[i]] = pos
        pos += 1
#len(burst_list['weibo'])

In [134]:
stream_burst_cdict = dict()
for key,value in stream_burst_train_dict.items():
    change_list = burst_list[key].keys()
    for i,line in enumerate(value):
        change_line = [min(change_list, key=lambda x:abs(x-i)) for i in line]
        value[i] = change_line
    stream_burst_cdict[key] = value

In [135]:
burst_start_state = dict()
burst_end_state = dict()
#print(stream_burst_cdict['hupu'])
for key,value in stream_burst_cdict.items():
    burst_start_state[key] = pd.Series([burst_list[key][x[0]] for x in value]).value_counts()
    burst_end_state[key] = pd.Series([burst_list[key][x[-1]] for x in value]).value_counts()
    burst_start_state[key] = burst_start_state[key]/burst_start_state[key].sum()
    burst_end_state[key] = burst_end_state[key]/burst_end_state[key].sum()
#burst_start_state['weibo']

In [136]:
#burst transition matrix
burst_transition_matrix = dict()
#print(stream_burst_cdict['hupu'])
#for stream in stream_burst_cdict['hupu']:
 #   print(len(stream))
for key,value in stream_burst_cdict.items():
    shape = (len(burst_list[key]),len(burst_list[key]))
    transition = pd.DataFrame(np.zeros(shape))
    for line in value:
        for i,x in enumerate(line):
            if i >= len(line)-1:
                break
            transition.iloc[burst_list[key][x], burst_list[key][line[i+1]]] += 1
    burst_transition_matrix[key] = transition.apply(lambda x:x/x.sum(),axis = 'columns').fillna(0)
#burst_transition_matrix['weibo']

In [137]:
#type markov train
def train_markov(line, start_state, end_state, transition_matrix):
    result = 0
    try:
        result = start_state[line[0]]
        #print('s' + str(result))
    except Exception:
        pass
    for i,x in enumerate(line):
        if i == len(line)-1:
            try:
                result *= end_state[line[-1]]
                #print('e' + str(result))
            except Exception:
                result *=0
            return pow(result, 1/len(line))
        result *= transition_matrix.iloc[x,line[i+1]]
        #print(str(x)+','+str(line[i+1])+':'+str(transition_matrix.iloc[x,line[i+1]]))
        #print(result)
type_markov_train = dict()
for key,value in stream_type_train_dict.items():
    train_data = list()
    for line in value:
        data = [train_markov(line, type_start_state[k], type_end_state[k], type_transition_matrix[k]) for k in type_start_state.keys()]
        train_data.append(data)
    type_markov_train[key] = train_data
#print(type_markov_train['weibo'][0])

In [138]:
#type markov test
type_markov_test = dict()
for key,value in stream_type_test_dict.items():
    test_data = list()
    for line in value:
        data = [train_markov(line, type_start_state[k], type_end_state[k], type_transition_matrix[k]) for k in type_start_state.keys()]
        test_data.append(data)
    type_markov_test[key] = test_data
print(type_markov_test['weibo'][0])

[0.27335765523346506, 0.0, 0.60976587427481632, 0.0, 0.56999872237874782, 0.28122696451645235, 0.0, 0.10527008591045733, 0.0, 0.0]


In [139]:
#length markov train
def train_cmarkov(line, start_state, end_state, transition_matrix,key, trans_list):
    #print(key)
    line = [min(trans_list, key=lambda x:abs(x-i)) for i in line]
    #print(line)
    result = 0
    try:
        result = start_state[trans_list[line[0]]]
        #print('s' + str(result))
    except Exception:
        pass
    for i,x in enumerate(line):
        if i == len(line)-1:
            try:
                result *= end_state[trans_list[line[-1]]]
                #print('e' + ','+str(result))
            except Exception:
                #print('e')
                result *=0
            return pow(result, 1/len(line))
        result *= transition_matrix.iloc[trans_list[x],trans_list[line[i+1]]]
        #print(str(trans_list[x])+','+str(trans_list[line[i+1]])+':'+str(transition_matrix.iloc[trans_list[x],trans_list[line[i+1]]]))
        #print(result)
length_markov_train = dict()
for key,value in stream_length_train_dict.items():
    train_data = list()
    #print(key)
    for line in value:
        #print(line)
        #data_c = train_cmarkov(line, length_start_state[key], length_end_state[key], length_transition_matrix[key], key, length_list[key])
        data = [train_cmarkov(line, length_start_state[k], length_end_state[k], length_transition_matrix[k], k, length_list[k]) for k in length_start_state.keys()]
        train_data.append(data)
    length_markov_train[key] = train_data
#length_markov_train['weibo'][0]

In [140]:
length_markov_test = dict()
for key,value in stream_length_test_dict.items():
    test_data = list()
    #print(key)
    for line in value:
        #print(line)
        #data_c = test_cmarkov(line, lengthf_start_state[key], length_end_state[key], length_transition_matrix[key], key, length_list[key])
        data = [train_cmarkov(line, length_start_state[k], length_end_state[k], length_transition_matrix[k], k, length_list[k]) for k in length_start_state.keys()]
        test_data.append(data)
    length_markov_test[key] = test_data
#length_markov_test['weibo'][0]

In [141]:
burst_markov_train = dict()
for key,value in stream_burst_train_dict.items():
    train_data = list()
    #print(key)
    for line in value:
        #print(line)
        #data_c = train_cmarkov(line, burst_start_state[key], burst_end_state[key], burst_transition_matrix[key], key, burst_list[key])
        data = [train_cmarkov(line, burst_start_state[k], burst_end_state[k], burst_transition_matrix[k], k, burst_list[k]) for k in burst_start_state.keys()]
        train_data.append(data)
    burst_markov_train[key] = train_data
#print(burst_markov_train['weibo'][0])

In [142]:
burst_markov_test = dict()
for key,value in stream_burst_test_dict.items():
    test_data = list()
    #print(key)
    for line in value:
        #print(line)
        #data_c = test_cmarkov(line, burst_start_state[key], burst_end_state[key], burst_transition_matrix[key], key, burst_list[key])
        data = [train_cmarkov(line, burst_start_state[k], burst_end_state[k], burst_transition_matrix[k], k, burst_list[k]) for k in burst_start_state.keys()]
        test_data.append(data)
    burst_markov_test[key] = test_data
#print(burst_markov_test['weibo'][0])
print('end2')

end2


In [143]:
if N != -1:
    train_path = root_dir + 'Experiment/MarkovModel/CsvFile/' + date + '/train_' + str(N) + "_" + str(Proportion) + '.csv'
else:
    train_path = root_dir + 'Experiment/MarkovModel/CsvFile/' + date + '/train_all_' + str(Proportion) + '.csv'
print(train_path)
train_data_dict = dict()
for key,value in type_markov_train.items():
    data = pd.concat([pd.DataFrame(value),pd.DataFrame(length_markov_train[key]), pd.DataFrame(burst_markov_train[key])], axis=1)
    data['label'] = key
    train_data_dict[key] = data
train_data_df = pd.concat([value for value in train_data_dict.values()],axis=0)
train_data_df.to_csv(train_path)
print('end2')

/Users/Leo/Documents/github/GradProj/Experiment/MarkovModel/CsvFile/noProxy/All/train_15_0.8.csv
end2


In [144]:
if N != -1:
    test_path = root_dir + 'Experiment/MarkovModel/CsvFile/' + date + '/test_' + str(N) + "_" + str(Proportion) + '.csv'
else:
    test_path = root_dir + 'Experiment/MarkovModel/CsvFile/' + date + '/test_all_' + str(Proportion) + '.csv'
    
test_data_dict = dict()
for key,value in type_markov_test.items():
    data = pd.concat([pd.DataFrame(value),pd.DataFrame(length_markov_test[key]), pd.DataFrame(burst_markov_test[key])], axis=1)
    data['label'] = key
    test_data_dict[key] = data
test_data_df = pd.concat([value for value in test_data_dict.values()],axis=0)
test_data_df.to_csv(test_path)
print('end2')

end2


In [145]:
#randomforest
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import accuracy_score
from sklearn.svm import SVC
x_train = train_data_df.iloc[:,0:5].values.copy()
y_train = train_data_df.iloc[:,-1].values.copy()
classifer = RandomForestClassifier()
classifer.fit(x_train,y_train)
x_test = test_data_df.iloc[:,0:5].values.copy()
y_test = test_data_df.iloc[:,-1].values.copy()
y_pred = classifer.predict(x_test)
accuracy_score(y_test, y_pred)

0.62448132780082988